In [15]:
import torch

# Load the model onto the CPU
AlexNet_Model = torch.load('AlexNet_Model.pt', map_location=torch.device('cpu'))



In [16]:
import torchvision.transforms as transforms
transform = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

In [17]:

import torch
from PIL import Image

classes = ('Airplane', 'Car', 'Bird', 'Cat', 'Deer', 'Dog', 'Frog', 'Horse', 'Ship', 'Truck')
# Define a function to preprocess the image
def preprocess_image(image_path):
    image = Image.open(image_path)
    image = transform(image).unsqueeze(0)
    return image

# Define the image paths
image_paths = [
    "car.jpeg"
]

# Preprocess the images
preprocessed_images = [preprocess_image(image_path) for image_path in image_paths]

# Make predictions
with torch.no_grad():
    predictions = AlexNet_Model(torch.cat(preprocessed_images, dim=0))

# Get the predicted probabilities for each class
predicted_probabilities = torch.nn.functional.softmax(predictions, dim=1)

# Print the probabilities for each class sorted by probability
for image_path, probabilities in zip(image_paths, predicted_probabilities):
    print(f"Image: {image_path}")
    sorted_indices = torch.argsort(probabilities, descending=True)
    for idx in sorted_indices:
        class_name = classes[idx]
        prob = probabilities[idx].item()
        print(f"Class: {class_name}, Probability: {prob}")


Image: car.jpeg
Class: Car, Probability: 1.0
Class: Truck, Probability: 1.9733740683203216e-11
Class: Ship, Probability: 1.0144151279612226e-16
Class: Airplane, Probability: 8.654194920607349e-20
Class: Frog, Probability: 5.849379056607012e-28
Class: Deer, Probability: 2.1034692384348658e-29
Class: Bird, Probability: 8.280908192503261e-30
Class: Horse, Probability: 3.741535700249233e-30
Class: Cat, Probability: 4.912921745335171e-31
Class: Dog, Probability: 1.9247921025898383e-33


In [11]:
import torch
from PIL import Image
import torchvision.transforms as transforms
import gradio as gr
import numpy as np

# Load the model onto the CPU
AlexNet_Model = torch.load('AlexNet_Model.pt', map_location=torch.device('cpu'))

transform = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

classes = ('Airplane', 'Car', 'Bird', 'Cat', 'Deer', 'Dog', 'Frog', 'Horse', 'Ship', 'Truck')

# Define a function to preprocess the image
def preprocess_image(image):
    if isinstance(image, np.ndarray):
        image = Image.fromarray(image)
    image = transform(image).unsqueeze(0)
    return image

# Define the prediction function
def predict(image):
    image = preprocess_image(image)
    with torch.no_grad():
        predictions = AlexNet_Model(image)

    # Get the predicted probabilities for each class
    predicted_probabilities = torch.nn.functional.softmax(predictions, dim=1)
    results = []
    for probabilities in (predicted_probabilities):
        sorted_indices = torch.argsort(probabilities, descending=True)
        for idx in sorted_indices:
            class_name = classes[idx]
            prob = probabilities[idx].item()
            #print(f"Class: {class_name}, Probability: {prob}")
            results.append((class_name, prob))


    return {class_name: prob for class_name, prob in results}

# Create Gradio interface
iface = gr.Interface(predict, 
                     inputs="image", 
                     outputs="label", 
                     title="AlexNet Image Classifier",
                     description="Classify images into one of 10 classes: Airplane, Car, Bird, Cat, Deer, Dog, Frog, Horse, Ship, or Truck.")
iface.launch()


Running on local URL:  http://127.0.0.1:7868

To create a public link, set `share=True` in `launch()`.


[('Car', 1.0), ('Truck', 1.9733740683203216e-11), ('Ship', 1.0144151279612226e-16), ('Airplane', 8.654194920607349e-20), ('Frog', 5.849379056607012e-28), ('Deer', 2.1034692384348658e-29), ('Bird', 8.280908192503261e-30), ('Horse', 3.741535700249233e-30), ('Cat', 4.912921745335171e-31), ('Dog', 1.9247921025898383e-33)]
[('Airplane', 0.5250793695449829), ('Truck', 0.3982219994068146), ('Car', 0.05421096831560135), ('Ship', 0.022192474454641342), ('Dog', 8.419439836870879e-05), ('Cat', 7.965308031998575e-05), ('Frog', 7.490476127713919e-05), ('Horse', 2.9290411475813016e-05), ('Bird', 2.588589813967701e-05), ('Deer', 1.2184905244794209e-06)]
